random forest for refined dataset
- imputed with mean value of each column
- eliminate outliers and leverges after normalized

some observations:
- the model contructed by not normalized dataset is as good as the normalized dataset.

In [1]:
%matplotlib inline
import pandas as pd
import numpy as np

import matplotlib.pyplot as plt
import seaborn as sns

In [2]:
from sklearn.ensemble import RandomForestRegressor

from sklearn.preprocessing import normalize
from sklearn.impute import SimpleImputer
from sklearn.model_selection import train_test_split

from sklearn.model_selection import RandomizedSearchCV, GridSearchCV, cross_val_score
from sklearn.metrics import mean_squared_error, r2_score

from sklearn import tree
import joblib

import scipy

In [3]:
plt.rcParams["figure.figsize"] = (15, 10)

## load data

In [4]:
pth_data = '../processed_data/train_refine_not_norm_min.csv'
df_refine = pd.read_csv(pth_data)

In [5]:
df_refine

height  weight  gender        bmi   age      rh  heart_rate  \
0      1.63    50.0     1.0  18.818924  23.0  39.890   70.500000   
1      1.74    65.0    -1.0  21.469150  23.0  51.680   76.298872   
2      1.77    68.0    -1.0  21.705129  24.0  55.748   66.000000   
3      1.63    50.0     1.0  18.818924  23.0  34.850   74.000000   
4      1.77    58.0    -1.0  18.513199  23.0  51.275   97.000000   
..      ...     ...     ...        ...   ...     ...         ...   
280    1.63    50.0     1.0  18.818924  23.0  55.330   65.000000   
281    1.69    75.0    -1.0  26.259585  24.0  31.690   70.000000   
282    1.69    75.0    -1.0  26.259585  24.0  25.660  105.000000   
283    1.71    64.0    -1.0  21.887076  27.0  42.280   59.000000   
284    1.71    64.0    -1.0  21.887076  27.0  56.110   70.000000   

     stress_level  skin_temp       eda   Clo  Act  env_temp  
0       10.000000  32.215000  0.146231  0.50  1.0    76.876  
1       23.987342  31.672874  0.877379  0.36  1.0    80.206  
2        6.000000  33.353000  0.033414  0.54  1.0    74.467  
3       20.000000  31.672874  0.068829  0.50  1.0    74.964  
4       76.500000  32.215000  0.006481  0.36  1.0    77.770  
..            ...        ...       ...   ...  ...       ...  
280      9.000000  31.672874  0.009863  0.50  0.8    76.703  
281      0.000000  32.007000  0.012317  0.36  1.0    74.791  
282     23.987342  30.484000  0.002907  0.36  1.8    75.139  
283     23.000000  33.996000  0.068711  0.74  1.0    75.484  
284     24.000000  34.073000  0.107164  0.74  1.0    69.449  

[285 rows x 13 columns]

In [6]:
df_refine.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 285 entries, 0 to 284
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   height        285 non-null    float64
 1   weight        285 non-null    float64
 2   gender        285 non-null    float64
 3   bmi           285 non-null    float64
 4   age           285 non-null    float64
 5   rh            285 non-null    float64
 6   heart_rate    285 non-null    float64
 7   stress_level  285 non-null    float64
 8   skin_temp     285 non-null    float64
 9   eda           285 non-null    float64
 10  Clo           285 non-null    float64
 11  Act           285 non-null    float64
 12  env_temp      285 non-null    float64
dtypes: float64(13)
memory usage: 29.1 KB


## data process

### X & y

In [9]:
X_data = df_refine[['height', 'weight', 'gender', 'bmi', 'age', 'rh', \
                      'heart_rate', 'stress_level', 'skin_temp', 'eda', \
                      'Clo', 'Act']]

In [10]:
X_cols_name = X_data.columns

In [11]:
y_data = df_refine['env_temp']

## random forest (1st try)

In [12]:
X_train, X_test, y_train, y_test = train_test_split(X_data, y_data, test_size=0.2, random_state=1208)

In [13]:
rfr = RandomForestRegressor(random_state=1208)

In [14]:
rfr.fit(X_train, y_train)

RandomForestRegressor(random_state=1208)

In [15]:
y_pred = rfr.predict(X_test)

In [16]:
# mean squared error
mean_squared_error(y_test, y_pred)

0.714701300061412

In [17]:
# R2 score
r2_score(y_test, y_pred)

0.7392511667320252

much better than the basic linear regression

## tuning hyperparameter
cross validation

### define hyper-param range for random search

In [18]:
# Number of trees in random forest
n_estimators = [int(x) for x in np.linspace(start = 200, stop = 2000, num = 10)]

# Number of features to consider at every split
max_features = ['auto', 'sqrt']

# Maximum number of levels in tree
max_depth = [int(x) for x in np.linspace(10, 110, num = 11)]
max_depth.append(None)

# Minimum number of samples required to split a node
min_samples_split = [2, 5, 10, 15, 20]

# Minimum number of samples required at each leaf node
min_samples_leaf = [1, 2, 4, 8, 16]

# Complexity parameter used for Minimal Cost-Complexity Pruning.
# ccp_alpha = [0.00001, 0.0005, 0.0001, 0.0005]
    
# Create the random grid
random_grid = {'n_estimators': n_estimators,
               'max_features': max_features,
               'max_depth': max_depth,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf}

In [19]:
random_grid

{'n_estimators': [200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000],
 'max_features': ['auto', 'sqrt'],
 'max_depth': [10, 20, 30, 40, 50, 60, 70, 80, 90, 100, 110, None],
 'min_samples_split': [2, 5, 10, 15, 20],
 'min_samples_leaf': [1, 2, 4, 8, 16]}

### random search
Use the random grid to search for best hyperparameters (approximately)
- 5-fold cross validation

In [20]:
rfr = RandomForestRegressor()

In [21]:
rfr_random = RandomizedSearchCV(estimator=rfr, 
                               param_distributions=random_grid, 
                               n_iter=100, 
                               cv=5, 
                               verbose=2, 
                               random_state=1208, 
                               n_jobs=-1,
                               scoring='r2')

In [22]:
# Fit the random search model
# Use R^2 as score method
rfr_random.fit(X_data, y_data)

Fitting 5 folds for each of 100 candidates, totalling 500 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 12 concurrent workers.
[Parallel(n_jobs=-1)]: Done  17 tasks      | elapsed:    5.3s
[Parallel(n_jobs=-1)]: Done 138 tasks      | elapsed:   27.0s
[Parallel(n_jobs=-1)]: Done 341 tasks      | elapsed:  1.0min
[Parallel(n_jobs=-1)]: Done 500 out of 500 | elapsed:  1.5min finished


RandomizedSearchCV(cv=5, estimator=RandomForestRegressor(), n_iter=100,
                   n_jobs=-1,
                   param_distributions={'max_depth': [10, 20, 30, 40, 50, 60,
                                                      70, 80, 90, 100, 110,
                                                      None],
                                        'max_features': ['auto', 'sqrt'],
                                        'min_samples_leaf': [1, 2, 4, 8, 16],
                                        'min_samples_split': [2, 5, 10, 15, 20],
                                        'n_estimators': [200, 400, 600, 800,
                                                         1000, 1200, 1400, 1600,
                                                         1800, 2000]},
                   random_state=1208, scoring='r2', verbose=2)

In [23]:
rfr_random.best_params_

{'n_estimators': 200,
 'min_samples_split': 2,
 'min_samples_leaf': 1,
 'max_features': 'auto',
 'max_depth': None}

In [24]:
rfr_random.best_score_

0.5623065237264487

### Grid Search
Random search allowed us to narrow down the range for each hyperparameter. Now that we know where to concentrate our search, we can explicitly specify every combination of settings to try.

In [25]:
param_grid = {
    'n_estimators': [50, 100, 200, 300, 400],
    'min_samples_split': [1, 2, 3],
    'min_samples_leaf': [1, 2, 3],
    'max_features': [2, 3, 4, 5],
    'max_depth': [1, 5, 10, 15, 20, None]
}

In [26]:
rfr = RandomForestRegressor()

In [27]:
grid_search = GridSearchCV(estimator = rfr, 
                           param_grid = param_grid, 
                           cv = 5, 
                           n_jobs = -1, 
                           verbose = 2,
                           scoring='r2')

In [28]:
grid_search.fit(X_data, y_data)

Fitting 5 folds for each of 1080 candidates, totalling 5400 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 12 concurrent workers.
[Parallel(n_jobs=-1)]: Done  17 tasks      | elapsed:    0.2s
[Parallel(n_jobs=-1)]: Done 252 tasks      | elapsed:    5.8s
[Parallel(n_jobs=-1)]: Done 658 tasks      | elapsed:   15.5s
[Parallel(n_jobs=-1)]: Done 1224 tasks      | elapsed:   28.9s
[Parallel(n_jobs=-1)]: Done 1954 tasks      | elapsed:   48.6s
[Parallel(n_jobs=-1)]: Done 2844 tasks      | elapsed:  1.2min
[Parallel(n_jobs=-1)]: Done 3898 tasks      | elapsed:  1.6min
[Parallel(n_jobs=-1)]: Done 5112 tasks      | elapsed:  2.2min
[Parallel(n_jobs=-1)]: Done 5400 out of 5400 | elapsed:  2.3min finished


GridSearchCV(cv=5, estimator=RandomForestRegressor(), n_jobs=-1,
             param_grid={'max_depth': [1, 5, 10, 15, 20, None],
                         'max_features': [2, 3, 4, 5],
                         'min_samples_leaf': [1, 2, 3],
                         'min_samples_split': [1, 2, 3],
                         'n_estimators': [50, 100, 200, 300, 400]},
             scoring='r2', verbose=2)

In [29]:
grid_search.best_params_

{'max_depth': 20,
 'max_features': 5,
 'min_samples_leaf': 1,
 'min_samples_split': 2,
 'n_estimators': 300}

In [30]:
grid_search.best_score_

0.5596149239387419

### validate the result

In [31]:
best_params = grid_search.best_params_

In [32]:
rfr = RandomForestRegressor(random_state=1208)

In [33]:
rfr.set_params(**best_params)

RandomForestRegressor(max_depth=20, max_features=5, n_estimators=300,
                      random_state=1208)

In [34]:
rfr_cv_mse = cross_val_score(rfr, X_data, y_data, scoring='neg_mean_squared_error', cv=5)

In [35]:
rfr_cv_mse

array([-1.6352623 , -1.22095044, -1.90560943, -1.40110021, -2.69703955])

In [36]:
np.abs(rfr_cv_mse.mean())

1.7719923869344392

In [37]:
rfr_cv_r2 = cross_val_score(rfr, X_data, y_data, scoring='r2', cv=5)

In [38]:
rfr_cv_r2

array([0.52742065, 0.69459154, 0.543234  , 0.57176468, 0.34639283])

In [39]:
np.abs(rfr_cv_r2.mean())

0.5366807421723574

## final model

In [40]:
best_params = {'max_depth': 18,
    'max_features': 3,
    'min_samples_leaf': 1,
    'min_samples_split': 2,
    'n_estimators': 700}

In [41]:
rfr_best = RandomForestRegressor(random_state=1208)
rfr_best.set_params(**best_params)

RandomForestRegressor(max_depth=18, max_features=3, n_estimators=700,
                      random_state=1208)

In [42]:
rfr_best.fit(X_data, y_data)

RandomForestRegressor(max_depth=18, max_features=3, n_estimators=700,
                      random_state=1208)

### save model

In [43]:
filename = './min_random_forest_model.sav'
joblib.dump(rfr_best, filename)

['./min_random_forest_model.sav']

## visualization
pick a tree from the forest to visualize

In [44]:
plt.rcParams["figure.figsize"] = (600, 100)
a_tree = tree.plot_tree(rfr_best.estimators_[0], 
                        feature_names=X_data.columns, 
                        rounded=True,
                        filled=True,
                        fontsize=12)

### normalize
if want to do normalize, inset the below code after 2.1 X & y

In [10]:
X_array_normalize, X_norm = normalize(X_data, axis=0, return_norm=True)
X_data = pd.DataFrame(X_array_normalize, columns=X_cols_name)
display(X_data)
display(X_norm)